In [1]:
import os
import anndata
import logging
import numpy as np
import pandas as pd
from datetime import timedelta, datetime
import scanpy as sc
import seaborn as sns
import matplotlib.pyplot as plt
import leidenalg
import csv
from pandas import Timestamp
import re
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from scipy.stats import rankdata 
import scipy

In [3]:
import glob

In [5]:
random_state=2024
organized_data_dir ="/home/dhy/20241120/BRCA/GSE161529/"


In [13]:
path_to_fast ="/home/dhy/20241120/BRCA/GSE161529/"

In [6]:
# 获取所有样本文件夹
sample_dirs = [d for d in glob.glob(os.path.join(organized_data_dir, "*")) if os.path.isdir(d)]
sample_dirs

['/home/dhy/20241120/BRCA/GSE161529/GSM4909308_ER-MH0040-LN',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909266_N-MH0169-Total',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909304_ER-MH0163',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909298_ER-PM0360',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909303_ER-MH0151',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909307_ER-MH0040',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909258_N-NF-Epi',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909275_N-PM0372-Epi',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909305_ER-MH0029-7C',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909321_mER-MH0068-LN',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909283_TN-SH0106',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909276_N-PM0372-Total',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909282_TN-MH0135',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909265_N-PM0233-Total',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909315_ER-MH0167-T',
 '/home/dhy/20241120/BRCA/GSE161529/GSM4909264_N-N1B-Epi',
 '/home/dhy/20241120/BRCA/G

In [7]:
# 提取样本名称
sample_names = [os.path.basename(d) for d in sample_dirs]

# 创建 DataFrame，将样本名称保存为一列
df = pd.DataFrame({'Sample_Name': sample_names})


In [8]:
df

Sample_Name
0     GSM4909308_ER-MH0040-LN
1   GSM4909266_N-MH0169-Total
2        GSM4909304_ER-MH0163
3        GSM4909298_ER-PM0360
4        GSM4909303_ER-MH0151
..                        ...
64   GSM4909287_TN-B1-Tum0554
65       GSM4909279_B1-MH0023
66  GSM4909272_N-MH0021-Total
67     GSM4909309_ER-MH0043-T
68       GSM4909280_B1-MH0090

[69 rows x 1 columns]

In [9]:
sample_names 

['GSM4909308_ER-MH0040-LN',
 'GSM4909266_N-MH0169-Total',
 'GSM4909304_ER-MH0163',
 'GSM4909298_ER-PM0360',
 'GSM4909303_ER-MH0151',
 'GSM4909307_ER-MH0040',
 'GSM4909258_N-NF-Epi',
 'GSM4909275_N-PM0372-Epi',
 'GSM4909305_ER-MH0029-7C',
 'GSM4909321_mER-MH0068-LN',
 'GSM4909283_TN-SH0106',
 'GSM4909276_N-PM0372-Total',
 'GSM4909282_TN-MH0135',
 'GSM4909265_N-PM0233-Total',
 'GSM4909315_ER-MH0167-T',
 'GSM4909264_N-N1B-Epi',
 'GSM4909285_TN-B1-MH4031',
 'GSM4909273_N-MH275-Epi',
 'GSM4909314_ER-MH0064-LN',
 'GSM4909301_ER-MH0042',
 'GSM4909281_TN-MH0126',
 'GSM4909318_ER-MH0173-LN',
 'GSM4909261_N-PM0230-Total',
 'GSM4909292_HER2-MH0069',
 'GSM4909269_N-PM0342-Epi',
 'GSM4909257_N-PM0095-Total',
 'GSM4909278_B1-MH0033',
 'GSM4909302_ER-MH0025',
 'GSM4909256_N-PM0095-Epi',
 'GSM4909295_ER-AH0319',
 'GSM4909289_HER2-AH0308',
 'GSM4909296_ER-MH0001',
 'GSM4909299_ER-MH0114-T3',
 'GSM4909253_N-PM0092-Total',
 'GSM4909310_ER-MH0043-LN',
 'GSM4909290_HER2-PM0337',
 'GSM4909320_mER-MH0068-T',

In [10]:
def load_10x_h5_sampleid(path_to_fast, sample_name):
    x=sc.read_10x_mtx(path_to_fast + sample_name +
                      "/")
    x.obs["sample"]=sample_name
    x.obs["barcode_back"]=x.obs.index
    x.obs['Barcode']=x.obs.index
    x.obs['Barcode']=[re.sub("^([A-Z]*)-([0-9].*)$", "\\1-", x) for x in x.obs['Barcode']]
    x.obs['Barcode']=[m+str(n) for m,n in zip(x.obs['Barcode'],x.obs['sample'])]
    x.obs.index=x.obs['Barcode'].values
    x.write(path_to_fast + sample_name +"/"+ sample_name+ ".h5ad")
    return x

In [14]:
adata_list = [load_10x_h5_sampleid(path_to_fast, sample_name) for sample_name in sample_names ]
adata_GSE161529= adata_list[0].concatenate(adata_list[1:])

/home/dhy/.conda/envs/pyscenic5/lib/python3.10/site-packages/anndata/_core/anndata.py:1823: FutureWarning: The AnnData.concatenate method is deprecated in favour of the anndata.concat function. Please use anndata.concat instead.

See the tutorial for concat at: https://anndata.readthedocs.io/en/latest/concatenation.html
  warnings.warn(


In [15]:
path_to_fast

'/home/dhy/20241120/BRCA/GSE161529/'

In [16]:
adata_GSE161529.write("BRCA_adata_GSE161529.h5ad")


In [3]:
# 01 GSE132257

In [ ]:
#  03 GSE188711

In [48]:
all_samples=   ["GSM5688706_WGC","GSM5688707_JCA","GSM5688708_LS-CRC3",
                "GSM5688709_RS-CRC1","GSM5688710_R_CRC3","GSM5688711_R_CRC4"]

In [46]:
def load_10x_h5_sampleid(path_to_fast, sample_name):
    x=sc.read_10x_mtx(path_to_fast + sample_name +
                      "/data/")
    x.obs["sample"]=sample_name
    x.obs["barcode_back"]=x.obs.index
    x.obs['Barcode']=x.obs.index
    x.obs['Barcode']=[re.sub("^([A-Z]*)-([0-9].*)$", "\\1-", x) for x in x.obs['Barcode']]
    x.obs['Barcode']=[m+str(n) for m,n in zip(x.obs['Barcode'],x.obs['sample'])]
    x.obs.index=x.obs['Barcode'].values
    x.write(path_to_fast + sample_name +"/"+ sample_name+ ".h5ad")
    return x

In [49]:
adata_list = [load_10x_h5_sampleid(path_to_fast, sample_name) for sample_name in all_samples]
adata_GSE188711= adata_list[0].concatenate(adata_list[1:])

/home/dhy/.conda/envs/pyscenic5/lib/python3.10/site-packages/anndata/_core/anndata.py:1823: FutureWarning: The AnnData.concatenate method is deprecated in favour of the anndata.concat function. Please use anndata.concat instead.

See the tutorial for concat at: https://anndata.readthedocs.io/en/latest/concatenation.html
  warnings.warn(


In [119]:
adata_GSE188711.obs

sample        barcode_back  \
AAACCCAAGAGCAGTC-GSM5688706_WGC-0        GSM5688706_WGC  AAACCCAAGAGCAGTC-1   
AAACCCAAGGCATGGT-GSM5688706_WGC-0        GSM5688706_WGC  AAACCCAAGGCATGGT-1   
AAACCCATCCGTGGGT-GSM5688706_WGC-0        GSM5688706_WGC  AAACCCATCCGTGGGT-1   
AAACGAAAGGGCTGAT-GSM5688706_WGC-0        GSM5688706_WGC  AAACGAAAGGGCTGAT-1   
AAACGAAAGGTACATA-GSM5688706_WGC-0        GSM5688706_WGC  AAACGAAAGGTACATA-1   
...                                                 ...                 ...   
TTTGGTTTCTGGGATT-GSM5688711_R_CRC4-5  GSM5688711_R_CRC4  TTTGGTTTCTGGGATT-1   
TTTGTTGCACAAACGG-GSM5688711_R_CRC4-5  GSM5688711_R_CRC4  TTTGTTGCACAAACGG-1   
TTTGTTGGTAATGCTC-GSM5688711_R_CRC4-5  GSM5688711_R_CRC4  TTTGTTGGTAATGCTC-1   
TTTGTTGGTTGAGGAC-GSM5688711_R_CRC4-5  GSM5688711_R_CRC4  TTTGTTGGTTGAGGAC-1   
TTTGTTGTCTTCCCGA-GSM5688711_R_CRC4-5  GSM5688711_R_CRC4  TTTGTTGTCTTCCCGA-1   

                                                                 Barcode batch  
AAACCCAAGAGCAGTC-GSM5688706_WGC-0        AAACCCAAGAGCAGTC-GSM5688706_WGC     0  
AAACCCAAGGCATGGT-GSM5688706_WGC-0        AAACCCAAGGCATGGT-GSM5688706_WGC     0  
AAACCCATCCGTGGGT-GSM5688706_WGC-0        AAACCCATCCGTGGGT-GSM5688706_WGC     0  
AAACGAAAGGGCTGAT-GSM5688706_WGC-0        AAACGAAAGGGCTGAT-GSM5688706_WGC     0  
AAACGAAAGGTACATA-GSM5688706_WGC-0        AAACGAAAGGTACATA-GSM5688706_WGC     0  
...                                                                  ...   ...  
TTTGGTTTCTGGGATT-GSM5688711_R_CRC4-5  TTTGGTTTCTGGGATT-GSM5688711_R_CRC4     5  
TTTGTTGCACAAACGG-GSM5688711_R_CRC4-5  TTTGTTGCACAAACGG-GSM5688711_R_CRC4     5  
TTTGTTGGTAATGCTC-GSM5688711_R_CRC4-5  TTTGTTGGTAATGCTC-GSM5688711_R_CRC4     5  
TTTGTTGGTTGAGGAC-GSM5688711_R_CRC4-5  TTTGTTGGTTGAGGAC-GSM5688711_R_CRC4     5  
TTTGTTGTCTTCCCGA-GSM5688711_R_CRC4-5  TTTGTTGTCTTCCCGA-GSM5688711_R_CRC4     5  

[35693 rows x 4 columns]

In [54]:
adata_GSE188711.var

gene_ids    feature_types
RP11-34P13.3  ENSG00000243485  Gene Expression
FAM138A       ENSG00000237613  Gene Expression
OR4F5         ENSG00000186092  Gene Expression
RP11-34P13.7  ENSG00000238009  Gene Expression
RP11-34P13.8  ENSG00000239945  Gene Expression
...                       ...              ...
AC233755.2    ENSG00000277856  Gene Expression
AC233755.1    ENSG00000275063  Gene Expression
AC240274.1    ENSG00000271254  Gene Expression
AC213203.1    ENSG00000277475  Gene Expression
FAM231B       ENSG00000268674  Gene Expression

[33694 rows x 2 columns]

In [131]:
adata_GSE132465_GSE132257.obs

Patient  Class         Sample         Cell_type
SMC01-T_AAACCTGCATACGCCG         SMC01  Tumor        SMC01-T  Epithelial cells
SMC01-T_AAACCTGGTCGCATAT         SMC01  Tumor        SMC01-T  Epithelial cells
SMC01-T_AAACCTGTCCCTTGCA         SMC01  Tumor        SMC01-T  Epithelial cells
SMC01-T_AAACGGGAGGGAAACA         SMC01  Tumor        SMC01-T  Epithelial cells
SMC01-T_AAACGGGGTATAGGTA         SMC01  Tumor        SMC01-T  Epithelial cells
...                                ...    ...            ...               ...
SMC171-T-SING_TTTGGTTGTGTAACGG  SMC171  Tumor  SMC171-T-SING           T cells
SMC171-T-SING_TTTGTCAAGGCCATAG  SMC171  Tumor  SMC171-T-SING     Stromal cells
SMC171-T-SING_TTTGTCAAGGTGCTAG  SMC171  Tumor  SMC171-T-SING           T cells
SMC171-T-SING_TTTGTCACAGCATACT  SMC171  Tumor  SMC171-T-SING  Epithelial cells
SMC171-T-SING_TTTGTCAGTCTGGAGA  SMC171  Tumor  SMC171-T-SING  Epithelial cells

[82098 rows x 4 columns]

In [132]:
adata_GSE188711.obs["Sample"] = adata_GSE188711.obs["sample"]
adata_GSE188711.obs["Patient"] = adata_GSE188711.obs["sample"]
adata_GSE188711.obs["Class"] =  "Tumor"


In [134]:
com_genes2 = adata_GSE132465_GSE132257.var_names.intersection(adata_GSE188711.var_names)
com_genes2

Index(['A1BG', 'A1BG-AS1', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1', 'A2ML1-AS1',
       'A2ML1-AS2', 'A3GALT2', 'A4GALT',
       ...
       'ZXDC', 'ZYG11A', 'ZYG11B', 'ZYX', 'ZZEF1', 'ZZZ3', 'bP-21264C1.2',
       'bP-2171C21.3', 'bP-2189O9.3', 'hsa-mir-1253'],
      dtype='object', length=33660)

In [135]:
adata_GSE188711 = adata_GSE188711[:,com_genes2]
adata_GSE132465_GSE132257 = adata_GSE132465_GSE132257[:,com_genes2]

In [136]:
adata_GSE132465_GSE132257_adata_GSE188711 = sc.concat([adata_GSE132465_GSE132257,adata_GSE188711],
                                       join="inner",
                                       index_unique=None)

In [137]:
adata_GSE132465_GSE132257_adata_GSE188711

AnnData object with n_obs × n_vars = 117791 × 33660
    obs: 'Patient', 'Class', 'Sample'

In [ ]:
# 04 GSE178341

In [146]:
adata_GSE178341  =sc.read_10x_h5(path_to_fast + 
                         "GSE178341_crc10x_full_c295v4_submit.h5")

/home/dhy/.conda/envs/pyscenic5/lib/python3.10/site-packages/anndata/_core/anndata.py:1900: UserWarning: Variable names are not unique. To make them unique, call `.var_names_make_unique`.
  utils.warn_names_duplicates("var")
/home/dhy/.conda/envs/pyscenic5/lib/python3.10/site-packages/anndata/_core/anndata.py:1900: UserWarning: Variable names are not unique. To make them unique, call `.var_names_make_unique`.
  utils.warn_names_duplicates("var")


In [ ]:
# 读取注释文件
cell_annotation_GSE178341 = pd.read_csv(path_to_fast + 
                                        'GSE178341_crc10x_full_c295v4_submit_metatables02.csv', 
                                         index_col=0)

In [147]:
if adata_GSE178341.obs.index.equals(cell_annotation_GSE178341.index):
    print("yizhi ")
else:
    print("no")

yizhi 


In [148]:
adata_GSE178341.obs = adata_GSE178341.obs.join(cell_annotation_GSE178341)

In [151]:
adata_GSE178341

AnnData object with n_obs × n_vars = 370115 × 43113
    obs: 'Class', 'SOURCE_HOSPITAL', 'TISSUE_PROCESSING_TEAM', 'PROCESSING_TYPE', 'Sample', 'HistologicTypeSimple', 'MMR_IHC', 'MMRStatus', 'MLH1Status', 'MMRMLH1Tumor', 'TissueSite_detailed', 'TissueSiteSimple', 'HistologicGrade_detailed', 'HistologicGradeSimple', 'TumorStage', 'NodeStatus_detailed', 'NodeStatusSimple', 'MetastasisStatus', 'TumorSize', 'SizeQuantile', 'Patient', 'Sex', 'Age', 'Ethnicity', 'Race'
    var: 'gene_ids', 'feature_types', 'genome'

In [163]:
print(adata_GSE178341.var_names.is_unique)

True


In [162]:
adata_GSE178341.var_names_make_unique()

/home/dhy/.conda/envs/pyscenic5/lib/python3.10/site-packages/anndata/utils.py:241: UserWarning: Suffix used (-[0-9]+) to deduplicate index values may make index values difficult to interpret. There values with a similar suffixes in the index. Consider using a different delimiter by passing `join={delimiter}`Example key collisions generated by the make_index_unique algorithm: ['SNORD116-1', 'SNORD116-2', 'SNORD116-3', 'SNORD116-5', 'SNORD116-6']
  warnings.warn(


In [164]:
adata_GSE178341

AnnData object with n_obs × n_vars = 370115 × 43113
    obs: 'Class', 'SOURCE_HOSPITAL', 'TISSUE_PROCESSING_TEAM', 'PROCESSING_TYPE', 'Sample', 'HistologicTypeSimple', 'MMR_IHC', 'MMRStatus', 'MLH1Status', 'MMRMLH1Tumor', 'TissueSite_detailed', 'TissueSiteSimple', 'HistologicGrade_detailed', 'HistologicGradeSimple', 'TumorStage', 'NodeStatus_detailed', 'NodeStatusSimple', 'MetastasisStatus', 'TumorSize', 'SizeQuantile', 'Patient', 'Sex', 'Age', 'Ethnicity', 'Race'
    var: 'gene_ids', 'feature_types', 'genome'

In [152]:
adata_GSE132465_GSE132257_adata_GSE188711

AnnData object with n_obs × n_vars = 117791 × 33660
    obs: 'Patient', 'Class', 'Sample'

In [165]:
gene_1_3 = adata_GSE132465_GSE132257_adata_GSE188711.var_names
gene_4 = adata_GSE178341.var_names

In [169]:
com_g  = gene_1_3.intersection(gene_4)
com_g  = com_g.unique()

In [170]:
adata_GSE132465_GSE132257_adata_GSE188711= adata_GSE132465_GSE132257_adata_GSE188711[:,com_g].copy()
adata_GSE132465_GSE132257_adata_GSE188711

AnnData object with n_obs × n_vars = 117791 × 30893
    obs: 'Patient', 'Class', 'Sample'

In [171]:
adata_GSE178341= adata_GSE178341[:,com_g].copy()
adata_GSE178341

AnnData object with n_obs × n_vars = 370115 × 30893
    obs: 'Class', 'SOURCE_HOSPITAL', 'TISSUE_PROCESSING_TEAM', 'PROCESSING_TYPE', 'Sample', 'HistologicTypeSimple', 'MMR_IHC', 'MMRStatus', 'MLH1Status', 'MMRMLH1Tumor', 'TissueSite_detailed', 'TissueSiteSimple', 'HistologicGrade_detailed', 'HistologicGradeSimple', 'TumorStage', 'NodeStatus_detailed', 'NodeStatusSimple', 'MetastasisStatus', 'TumorSize', 'SizeQuantile', 'Patient', 'Sex', 'Age', 'Ethnicity', 'Race'
    var: 'gene_ids', 'feature_types', 'genome'

In [172]:
adata_GSE178341

AnnData object with n_obs × n_vars = 370115 × 30893
    obs: 'Class', 'SOURCE_HOSPITAL', 'TISSUE_PROCESSING_TEAM', 'PROCESSING_TYPE', 'Sample', 'HistologicTypeSimple', 'MMR_IHC', 'MMRStatus', 'MLH1Status', 'MMRMLH1Tumor', 'TissueSite_detailed', 'TissueSiteSimple', 'HistologicGrade_detailed', 'HistologicGradeSimple', 'TumorStage', 'NodeStatus_detailed', 'NodeStatusSimple', 'MetastasisStatus', 'TumorSize', 'SizeQuantile', 'Patient', 'Sex', 'Age', 'Ethnicity', 'Race'
    var: 'gene_ids', 'feature_types', 'genome'

In [173]:
adata_all_4 = sc.concat([adata_GSE132465_GSE132257_adata_GSE188711,adata_GSE178341],
                                       join="inner",
                                       index_unique=None)

In [174]:
adata_all_4.obs

Patient  Class   Sample
SMC01-T_AAACCTGCATACGCCG                 SMC01  Tumor  SMC01-T
SMC01-T_AAACCTGGTCGCATAT                 SMC01  Tumor  SMC01-T
SMC01-T_AAACCTGTCCCTTGCA                 SMC01  Tumor  SMC01-T
SMC01-T_AAACGGGAGGGAAACA                 SMC01  Tumor  SMC01-T
SMC01-T_AAACGGGGTATAGGTA                 SMC01  Tumor  SMC01-T
...                                        ...    ...      ...
C173_T_0_0_0_c1_v3_id-TTTGGAGTCATCGGGC    C173  Tumor   C173_T
C173_T_0_0_0_c1_v3_id-TTTGGAGTCTAGTGTG    C173  Tumor   C173_T
C173_T_0_0_0_c1_v3_id-TTTGTTGCAGCAATTC    C173  Tumor   C173_T
C173_T_0_0_0_c1_v3_id-TTTGTTGGTTCTGAGT    C173  Tumor   C173_T
C173_T_0_0_0_c1_v3_id-TTTGTTGTCGTTCCCA    C173  Tumor   C173_T

[487906 rows x 3 columns]

In [175]:
adata_all_4.write(path_to_fast +  "CRC_01.h5ad")
# 检查 TIMP1 在原始 counts 数据中的表达情况
timp1_expression_raw = adata_all_4[:, adata_all_4.var_names == "TIMP1"].X

# 查看原始表达值的类型和范围
print(f"数据类型: {type(timp1_expression_raw)}")
print(f"最大值: {timp1_expression_raw.max()}, 最小值: {timp1_expression_raw.min()}")

数据类型: <class 'anndata._core.views.SparseCSRView'>
最大值: 2581.0, 最小值: 0.0


In [1]:
adata_all_4

NameError: name 'adata_all_4' is not defined

In [ ]:
counts
